<a href="https://colab.research.google.com/github/KUrushi/toy_code/blob/main/bqml_tfma.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from IPython.display import clear_output
! pip install tensorflow-model-analysis==0.25.0
clear_output()

In [ ]:
import pandas as pd
import tensorflow as tf
import tensorflow_model_analysis as tfma
from google.colab import auth

auth.authenticate_user()

In [ ]:
PROJECT_ID = ""  # @param {type:"string"}

In [ ]:
%%bigquery --project $PROJECT_ID
CREATE MODEL IF NOT EXISTS
  `bqml_tutorial.natality_model` OPTIONS (model_type='linear_reg',
    input_label_cols=['weight_pounds']) AS
SELECT
  weight_pounds,
  is_male,
  gestation_weeks,
  mother_age,
  CAST(mother_race AS string) AS mother_race
FROM
  `bigquery-public-data.samples.natality`
WHERE
  weight_pounds IS NOT NULL
  AND MOD(ABS(farm_fingerprint(FORMAT("%d:%d:%d", year, month, day))),100) <= 1

Empty DataFrame
Columns: []
Index: []

In [ ]:
%%bigquery --project $PROJECT_ID --use_bqstorage_api df
SELECT
  *
FROM
  ML.PREDICT(MODEL `bqml_tutorial.natality_model`,
    (
    SELECT
      is_male,
      gestation_weeks,
      mother_age,
      state,
      weight_pounds,
      CAST(mother_race AS STRING) AS mother_race
    FROM
      `bigquery-public-data.samples.natality`
    WHERE
      weight_pounds IS NOT NULL
      AND MOD(ABS(farm_fingerprint(FORMAT("%d:%d:%d", year, month, day))),100) = 2 ))

In [ ]:
df['gestation_weeks'] = df['gestation_weeks'].fillna(-1).astype(int)
df['is_male'] = df['is_male'].astype(int)

In [ ]:
LABEL = 'weight_pounds'
metrics = [
    tfma.metrics.ExampleCount(name='example_count'),
    tf.keras.metrics.MeanSquaredError(name='mse'),
    tfma.metrics.MeanLabel(name='mean_label'),
    tfma.metrics.MeanPrediction(name='mean_prediction'),
    tfma.metrics.Calibration(name='calibration'),
]
metrics_specs = tfma.metrics.specs_from_metrics(metrics)
slicing_specs = [
  tfma.SlicingSpec(),
  tfma.SlicingSpec(feature_keys=['is_male']),
  tfma.SlicingSpec(feature_keys=['gestation_weeks']),
  tfma.SlicingSpec(feature_keys=['mother_age']),
  tfma.SlicingSpec(feature_keys=['state']),
  tfma.SlicingSpec(feature_keys=['gestation_weeks', 'mother_age'])
]
model_specs = [tfma.ModelSpec(prediction_key=f'predicted_{LABEL}', label_key=LABEL)]
eval_config = tfma.EvalConfig(
    model_specs=model_specs,
    metrics_specs=metrics_specs,
    slicing_specs=slicing_specs)

In [ ]:
result_ = tfma.analyze_raw_data(
  data=df,
  eval_config=eval_config,
)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


In [ ]:
tfma.view.render_slicing_metrics(result_)

In [ ]:
tfma.view.render_slicing_metrics(result_, slicing_spec=slicing_specs[1])

In [ ]:
tfma.view.render_slicing_metrics(result_, slicing_spec=slicing_specs[5])

In [ ]:
tfma.view.render_slicing_metrics(result_, slicing_column='mother_age')

In [ ]:
tfma.view.render_slicing_metrics(result_, slicing_column='state')